In [ ]:
import os
import itertools
import time
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import transforms
from torch.utils.data import DataLoader, Dataset
from PIL import Image
from tqdm import tqdm

# ========== Dataset ==========
class ImageDataset(Dataset):
    def __init__(self, root, split='train'):
        self.real_paths = sorted(os.listdir(os.path.join(root, split, 'photos')))
        self.sketch_paths = sorted(os.listdir(os.path.join(root, split, 'sketches')))
        self.real_folder = os.path.join(root, split, 'photos')
        self.sketch_folder = os.path.join(root, split, 'sketches')

        self.transform = transforms.Compose([
            transforms.Resize((128, 128)),  # Reduced size for faster training
            transforms.ToTensor(),
            transforms.Normalize((0.5,), (0.5,))
        ])

    def __len__(self):
        return min(len(self.real_paths), len(self.sketch_paths))

    def __getitem__(self, index):
        real_img = Image.open(os.path.join(self.real_folder, self.real_paths[index])).convert("RGB")
        sketch_img = Image.open(os.path.join(self.sketch_folder, self.sketch_paths[index])).convert("RGB")

        real = self.transform(real_img)
        sketch = self.transform(sketch_img)

        return {'real': real, 'sketch': sketch}

# ========== Generator ==========
class Generator(nn.Module):
    def __init__(self):
        super().__init__()
        def block(in_channels, out_channels, normalize=True):
            layers = [nn.Conv2d(in_channels, out_channels, 4, stride=2, padding=1)]
            if normalize:
                layers.append(nn.BatchNorm2d(out_channels))
            layers.append(nn.ReLU(inplace=True))
            return layers

        def deblock(in_channels, out_channels):
            layers = [nn.ConvTranspose2d(in_channels, out_channels, 4, stride=2, padding=1),
                      nn.BatchNorm2d(out_channels),
                      nn.ReLU(inplace=True)]
            return layers

        self.encoder = nn.Sequential(
            *block(3, 64, normalize=False),
            *block(64, 128),
            *block(128, 256),
            *block(256, 512)
        )

        self.decoder = nn.Sequential(
            *deblock(512, 256),
            *deblock(256, 128),
            *deblock(128, 64),
            nn.ConvTranspose2d(64, 3, 4, stride=2, padding=1),
            nn.Tanh()
        )

    def forward(self, x):
        return self.decoder(self.encoder(x))

# ========== Discriminator ==========
class Discriminator(nn.Module):
    def __init__(self):
        super().__init__()
        def block(in_channels, out_channels, normalize=True):
            layers = [nn.Conv2d(in_channels, out_channels, 4, stride=2, padding=1)]
            if normalize:
                layers.append(nn.BatchNorm2d(out_channels))
            layers.append(nn.LeakyReLU(0.2, inplace=True))
            return layers

        self.model = nn.Sequential(
            *block(3, 64, normalize=False),
            *block(64, 128),
            *block(128, 256),
            *block(256, 512),
            nn.Conv2d(512, 1, 4, padding=1)
        )

    def forward(self, img):
        return self.model(img)

# ========== Training ==========
def train_cycle_gan(data_root, save_path, num_epochs=10, batch_size=1):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    print(f"Using device: {device}")

    # Load data
    dataset = ImageDataset(root=data_root, split='train')
    dataloader = DataLoader(dataset, batch_size=batch_size, shuffle=True, num_workers=2)

    # Define models
    G = Generator().to(device)  # Sketch to Real
    F = Generator().to(device)  # Real to Sketch
    D_X = Discriminator().to(device)  # Discriminator for Sketch
    D_Y = Discriminator().to(device)  # Discriminator for Real

    # Losses
    criterion_GAN = nn.MSELoss()
    criterion_cycle = nn.L1Loss()
    criterion_identity = nn.L1Loss()

    # Optimizers
    lr = 0.0002
    beta1 = 0.5
    optimizer_G = optim.Adam(itertools.chain(G.parameters(), F.parameters()), lr=lr, betas=(beta1, 0.999))
    optimizer_D_X = optim.Adam(D_X.parameters(), lr=lr, betas=(beta1, 0.999))
    optimizer_D_Y = optim.Adam(D_Y.parameters(), lr=lr, betas=(beta1, 0.999))

    # Learning rate scheduler
    lr_scheduler_G = optim.lr_scheduler.StepLR(optimizer_G, step_size=5, gamma=0.5)
    lr_scheduler_D_X = optim.lr_scheduler.StepLR(optimizer_D_X, step_size=5, gamma=0.5)
    lr_scheduler_D_Y = optim.lr_scheduler.StepLR(optimizer_D_Y, step_size=5, gamma=0.5)

    for epoch in range(1, num_epochs + 1):
        print(f"\nEpoch [{epoch}/{num_epochs}]")
        epoch_start = time.time()

        for i, batch in enumerate(tqdm(dataloader)):
            iter_start = time.time()

            real_X = batch['sketch'].to(device)
            real_Y = batch['real'].to(device)

            # -------------------
            #  Train Generators
            # -------------------
            optimizer_G.zero_grad()

            # Identity loss
            loss_idt_Y = criterion_identity(G(real_Y), real_Y) * 5.0
            loss_idt_X = criterion_identity(F(real_X), real_X) * 5.0

            # GAN loss
            fake_Y = G(real_X)
            pred_fake_Y = D_Y(fake_Y)
            loss_GAN_XY = criterion_GAN(pred_fake_Y, torch.ones_like(pred_fake_Y))

            fake_X = F(real_Y)
            pred_fake_X = D_X(fake_X)
            loss_GAN_YX = criterion_GAN(pred_fake_X, torch.ones_like(pred_fake_X))

            # Cycle loss
            rec_X = F(fake_Y)
            loss_cycle_X = criterion_cycle(rec_X, real_X) * 10.0

            rec_Y = G(fake_X)
            loss_cycle_Y = criterion_cycle(rec_Y, real_Y) * 10.0

            # Total loss
            loss_G = loss_idt_X + loss_idt_Y + loss_GAN_XY + loss_GAN_YX + loss_cycle_X + loss_cycle_Y
            loss_G.backward()
            optimizer_G.step()

            # -----------------------
            #  Train Discriminator X
            # -----------------------
            optimizer_D_X.zero_grad()
            pred_real_X = D_X(real_X)
            pred_fake_X = D_X(fake_X.detach())
            loss_real_X = criterion_GAN(pred_real_X, torch.ones_like(pred_real_X))
            loss_fake_X = criterion_GAN(pred_fake_X, torch.zeros_like(pred_fake_X))
            loss_D_X = (loss_real_X + loss_fake_X) * 0.5
            loss_D_X.backward()
            optimizer_D_X.step()

            # -----------------------
            #  Train Discriminator Y
            # -----------------------
            optimizer_D_Y.zero_grad()
            pred_real_Y = D_Y(real_Y)
            pred_fake_Y = D_Y(fake_Y.detach())
            loss_real_Y = criterion_GAN(pred_real_Y, torch.ones_like(pred_real_Y))
            loss_fake_Y = criterion_GAN(pred_fake_Y, torch.zeros_like(pred_fake_Y))
            loss_D_Y = (loss_real_Y + loss_fake_Y) * 0.5
            loss_D_Y.backward()
            optimizer_D_Y.step()

            print(f"Iter {i}/{len(dataloader)} took {time.time() - iter_start:.2f}s")

        print(f"Epoch {epoch} took {time.time() - epoch_start:.2f}s")

        # Step LR scheduler
        lr_scheduler_G.step()
        lr_scheduler_D_X.step()
        lr_scheduler_D_Y.step()

        # Save models
        torch.save({'model_state_dict': G.state_dict()}, os.path.join(save_path, f"G_epoch_{epoch}.pth"))
        torch.save({'model_state_dict': F.state_dict()}, os.path.join(save_path, f"F_epoch_{epoch}.pth"))
        print(f"Saved model for epoch {epoch}")

    # Save final generators
    torch.save(G.state_dict(), os.path.join(save_path, "generator_sketch2face.pth"))
    torch.save(F.state_dict(), os.path.join(save_path, "generator_face2sketch.pth"))
    print("Final models saved for interface use.")

# ======= Run Training ========
data_root = "/kaggle/input/person-face-sketches"
save_path = "/kaggle/working"
train_cycle_gan(data_root, save_path, num_epochs=10, batch_size=1)


Using device: cuda

Epoch [1/10]


  0%|          | 4/20655 [00:01<1:33:20,  3.69it/s]

Iter 0/20655 took 1.10s
Iter 1/20655 took 0.04s
Iter 2/20655 took 0.04s
Iter 3/20655 took 0.05s
Iter 4/20655 took 0.05s


  0%|          | 10/20655 [00:01<36:43,  9.37it/s] 

Iter 5/20655 took 0.05s
Iter 6/20655 took 0.05s
Iter 7/20655 took 0.05s
Iter 8/20655 took 0.05s
Iter 9/20655 took 0.05s


...

 78%|███████▊  | 16073/20655 [12:51<03:39, 20.89it/s]

Iter 16068/20655 took 0.05s
Iter 16069/20655 took 0.05s
Iter 16070/20655 took 0.05s
Iter 16071/20655 took 0.05s
Iter 16072/20655 took 0.05s


 78%|███████▊  | 16076/20655 [12:51<03:40, 20.81it/s]

Iter 16073/20655 took 0.05s
Iter 16074/20655 took 0.05s
Iter 16075/20655 took 0.05s
Iter 16076/20655 took 0.05s
Iter 16077/20655 took 0.05s


 78%|███████▊  | 16082/20655 [12:51<03:40, 20.73it/s]

In [24]:
checkpoint_path = '/kaggle/working/generator_final.pth'

checkpoint = torch.load(checkpoint_path)

# Print the keys in the checkpoint
print(checkpoint.keys())


dict_keys(['epoch', 'model_state_dict', 'optimizer_state_dict'])


/tmp/ipykernel_31/1088013715.py:3: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(checkpoint_path)
